In [23]:
import pymssql

# SQL Server에 연결
try : 
    conn = pymssql.connect(
            server='220.85.109.247',  # 서버 IP 또는 호스트명
            user='sungmin',            # SQL Server 사용자 이름
            password='0691',           # 비밀번호
            database='SOFTCRM',         # 연결할 데이터베이스 이름
            tds_version="7.0",
    )
    # 커서 생성
    cursor = conn.cursor()

    # 예시 쿼리 실행 (테이블에서 데이터 조회)
    cursor.execute("""WITH COST_SUM AS (
    SELECT 
        CUST_NUM, 
        SUM(COST_PRICE) AS TOTAL_COST_PRICE
    FROM COSTPRICE
    GROUP BY CUST_NUM
    )
    SELECT c.CUST_NUM, c.CUST_NAME, c.BIRTH_DAY, c.JOB, c.ADDR1, c.ADDR2,
	e.EXAM_DATE, e.STOP_YN, e.CANCEL_CD,
	COALESCE(cs.TOTAL_COST_PRICE, 0) AS TOTAL_COST_PRICE,
	mn.category01_name as MOTIVE
    FROM CUSTOM c
    INNER JOIN EXAM e 
    ON c.CUST_NUM = e.CUST_NUM
    INNER JOIN RESERVATION R
	on c.CUST_NUM = R.CUST_NUM 
    LEFT JOIN COST_SUM cs ON c.CUST_NUM = cs.CUST_NUM 
    LEFT JOIN MOTIVE_NEW02 mn ON c.CUST_NUM = mn.CUST_NUM
    WHERE e.EXAM_DATE BETWEEN '2020-01-01' AND '2024-12-29'
    and mn.Idx =1
    and R.RESERVE_FLAG='m'
    AND R.RESERVE_STATE IN('I','H')
    AND NOT (e.CUST_NUM IN ('9999999999999', '8888888888888'))""")

    # 중복 제거를 위한 집합
    seen = set()

    # 결과 출력 (중복 제거)
    for row in cursor:
            if row not in seen:  # 중복 확인
                seen.add(row)    # 중복 방지 집합에 추가
                print(', '.join(map(str, row)))
except pymssql.DatabaseError as e:
        print(f"Database connection error: {e}")

finally:
    # 연결 종료
    if 'cursor' in locals():
        cursor.close()
    if 'conn' in locals():
        conn.close()



123918       , 손지영, 1982-02-28, 직장인, 서울 광진구 아차산로 549, , 2023-05-19, N,    , 50000.0000, 소개고객
12680        , 김선옥, 1960-03-23, 주부, 경기도 군포시 금산로21번길 14-1 (금정동), 102호, 2020-02-17, N,    , 7005400.0000, 소개고객
14058        , 김연진, 1961-06-14, 회사원, 전라남도 여수시 신월로 655 (국동, 서희스타힐스), 1111동 702호, 2020-03-19, N,    , 72000.0000, 소개미확인
172635       , 양경혜, 1985-08-31, 간호사, 경기 수원시 영통구 광교호수공원로 80, 106동306호, 2021-05-22, N,    , 2447000.0000, X고객지원
193148       , 정세미, 1987-03-10, 직장인, 울산 남구 삼산중로 83, 달동현대1차102동806호, 2020-01-11, N,    , 100000.0000, 홈페이지
2013197      , 김원철, 1983-01-19, 회사원, 서울시 성북구 서경로 31, 106동 902호, , 2022-02-08, N,    , 2362000.0000, 소개고객
2015408      , 김건희, 1998-09-04, 학생, 강원 철원군 서면 와수리 1171-83, , 2022-11-26, N,    , 2066000.0000, 소개고객
2021936      , 선주협, 1998-03-26, 취업준비/휴식중, 경기 남양주시 홍유릉로325번길 16 (금곡동, 인정프린스APT), 인정프린스아파트 102동 109호, 2020-09-22, N,    , 1870000.0000, 소개고객
2025185      , 이기헌, 1998-02-14, 학생, 서울 성북구 개운사길 22-2, 301호, 2021-07-30, N,    , 0.0000, 소개고객
2028119      , 조민지, 2005-09

In [70]:
import pandas as pd
df = pd.read_csv('/Users/bijyuwogseu/Desktop/test/crmdata.csv',
                 sep=',',           # 필요시 구분자 변경
                on_bad_lines='skip')
df.columns = ["Id","이름","생년월일","직업","주소1","주소2","검사일","예약1","예약2","가격","내원동기"]
df.index = range(1,len(df)+1)
df.info()
print('\n')
df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 77550 entries, 1 to 77550
Data columns (total 11 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Id      77550 non-null  int64  
 1   이름      77550 non-null  object 
 2   생년월일    77550 non-null  object 
 3   직업      77550 non-null  object 
 4   주소1     77550 non-null  object 
 5   주소2     77550 non-null  object 
 6   검사일     77550 non-null  object 
 7   예약1     77550 non-null  object 
 8   예약2     77550 non-null  object 
 9   가격      77550 non-null  float64
 10  내원동기    77550 non-null  object 
dtypes: float64(1), int64(1), object(9)
memory usage: 6.5+ MB




Id    이름         생년월일    직업                          주소1  \
1    12680   김선옥   1960-03-23    주부   경기도 군포시 금산로21번길 14-1 (금정동)   
2   172635   양경혜   1985-08-31   간호사        경기 수원시 영통구 광교호수공원로 80   
3   193148   정세미   1987-03-10   직장인                울산 남구 삼산중로 83   
4  2015408   김건희   1998-09-04    학생        강원 철원군 서면 와수리 1171-83   
5  2025185   이기헌   1998-02-14    학생             서울 성북구 개운사길 22-2   

               주소2          검사일 예약1   예약2         가격    내원동기  
1             102호   2020-02-17   N        7005400.0    소개고객  
2         106동306호   2021-05-22   N        2447000.0   X고객지원  
3   달동현대1차102동806호   2020-01-11   N         100000.0    홈페이지  
4                    2022-11-26   N        2066000.0    소개고객  
5             301호   2021-07-30   N              0.0    소개고객

In [71]:
df.head().isnull().sum(axis=0)

df_dup = df.duplicated()
df_dup

1        False
2        False
3        False
4        False
5        False
         ...  
77546    False
77547    False
77548    False
77549    False
77550    False
Length: 77550, dtype: bool

In [45]:
print(df['내원동기'].unique())
print('\n')
print(df['직업'].unique())

[' 소개고객' ' X고객지원' ' 홈페이지' ' 소개미확인' ' B2B(군인)' ' B2B(기업)' ' 소개직원' ' 광고'
 ' VIP고객관리팀' ' 기타' ' 바이럴' ' X인터넷' ' B2B(비앤빛)' ' 프로모션' ' B2B(백내장)' ' 제휴'
 ' 검색' ' 명동밝은세상안과' ' Doctor' ' X인터넷검색' ' 아이앤유' ' 인터넷' ' X제휴 ㄹ~ㅅ' ' E업체소개'
 ' E외래진료']


[' 주부' ' 간호사' ' 직장인' ... ' 의대생' ' 필라테스 강사' ' 레스토랑매니저']


In [91]:
df['new_Date'] = pd.to_datetime(df['검사일'])
df['Date_yr'] = df['new_Date'].dt.to_period(freq='Y')
df['Date_m'] = df['new_Date'].dt.to_period(freq='M')

print(df.head())
print('\n')
print(df.info())

        Id    이름         생년월일    직업                          주소1  \
1    12680   김선옥   1960-03-23    주부   경기도 군포시 금산로21번길 14-1 (금정동)   
2   172635   양경혜   1985-08-31   간호사        경기 수원시 영통구 광교호수공원로 80   
3   193148   정세미   1987-03-10   직장인                울산 남구 삼산중로 83   
4  2015408   김건희   1998-09-04    학생        강원 철원군 서면 와수리 1171-83   
5  2025185   이기헌   1998-02-14    학생             서울 성북구 개운사길 22-2   

               주소2          검사일 예약1   예약2         가격    내원동기   new_Date  \
1             102호   2020-02-17   N        7005400.0    소개고객 2020-02-17   
2         106동306호   2021-05-22   N        2447000.0   X고객지원 2021-05-22   
3   달동현대1차102동806호   2020-01-11   N         100000.0    홈페이지 2020-01-11   
4                    2022-11-26   N        2066000.0    소개고객 2022-11-26   
5             301호   2021-07-30   N              0.0    소개고객 2021-07-30   

  Date_yr   Date_m 가격등급  price_rounded  
1    2020  2020-02   고가      7005400.0  
2    2021  2021-05   고가      2447000.0  
3    2020  2020-0

In [92]:
df['생년월일'] = df['생년월일'].astype(str)
dates = df['생년월일'].str.split('-')

dates.head()

1    [ 1960, 03, 23]
2    [ 1985, 08, 31]
3    [ 1987, 03, 10]
4    [ 1998, 09, 04]
5    [ 1998, 02, 14]
Name: 생년월일, dtype: object

In [100]:
def classify_price(가격):
    if 가격 <500000 :
        return '저가'
    elif 50 <= 가격 <2500000 :
        return '중가' 
    else :
        return '고가'

# 가격클래스에 따라 'price_class'열 추가
df['가격등급'] = df['가격'].apply(classify_price)


df.head(10)

Id    이름         생년월일         직업                              주소1  \
1     12680   김선옥   1960-03-23         주부       경기도 군포시 금산로21번길 14-1 (금정동)   
2    172635   양경혜   1985-08-31        간호사            경기 수원시 영통구 광교호수공원로 80   
3    193148   정세미   1987-03-10        직장인                    울산 남구 삼산중로 83   
4   2015408   김건희   1998-09-04         학생            강원 철원군 서면 와수리 1171-83   
5   2025185   이기헌   1998-02-14         학생                 서울 성북구 개운사길 22-2   
6   2028119   조민지   2005-09-19         학생                 서울 서초구 방배로43길 21   
7   2028549   조하은   2003-05-21        대학생                   서울 노원구 노해로 508   
8   2028678   박찬진   1998-08-01         학생               경기 고양시 덕양구 향기로 112   
9   2029330   전윤배   1997-08-28       프리랜서       경기 남양주시 진건오남로 781-17 두산아파트   
10  2042265   이지선   1995-04-01   취업준비/휴식중   경기도 광명시 철산3동 쌍마한신아파트 103동 509호   

                  주소2          검사일 예약1   예약2         가격    내원동기   new_Date  \
1                102호   2020-02-17   N        7005400.0    소개고객 2020-02-17   
2            106동306호   2021-05-22   N        2447000.0   X고객지원 2021-05-22   
3      달동현대1차102동806호   2020-01-11   N         100000.0    홈페이지 2020-01-11   
4                       2022-11-26   N        2066000.0    소개고객 2022-11-26   
5                301호   2021-07-30   N              0.0    소개고객 2021-07-30   
6            3동 1010호   2024-02-03   N        3960000.0    소개고객 2024-02-03   
7           624동 702호   2022-05-28   N        2272000.0    소개고객 2022-05-28   
8    DMC하우스디 203동 301   2020-05-08   N        5400000.0   소개미확인 2020-05-08   
9            103동102호   2021-03-31   N        2072000.0   소개미확인 2021-03-31   
10                      2024-12-16   N        2700000.0    홈페이지 2024-12-16   

   Date_yr   Date_m 가격등급  
1     2020  2020-02   고가  
2     2021  2021-05   중가  
3     2020  2020-01   저가  
4     2022  2022-11   중가  
5     2021  2021-07   저가  
6     2024  2024-02   고가  
7     2022  2022-05   중가  
8     2020  2020-05   고가  
9     2021  2021-03   중가  
10    2024  2024-12   고가

In [103]:
grouped = df.groupby(['가격등급'], observed =True)
average = grouped.mean(numeric_only=True)

In [117]:
value_counts = df['직업'].value_counts()


# 상대 빈도 계산
relative_counts = df['직업'].value_counts(normalize=True)
print(value_counts)
print('\n')
print(relative_counts)


직업
직장인           29161
대학생           22963
취업준비(휴식)       6179
군인             3802
자영업/프리랜서       3632
              ...  
회사원/대학원생          1
속눈썹연장             1
학교실무사             1
야외 골프장코스관리        1
레스토랑매니저           1
Name: count, Length: 1209, dtype: int64


직업
직장인           0.376028
대학생           0.296106
취업준비(휴식)      0.079678
군인            0.049026
자영업/프리랜서      0.046834
                ...   
회사원/대학원생      0.000013
속눈썹연장         0.000013
학교실무사         0.000013
야외 골프장코스관리    0.000013
레스토랑매니저       0.000013
Name: proportion, Length: 1209, dtype: float64


In [121]:
#상위 10개만 출력
top_10 = value_counts.head(10)

#직업 열의 상배 빈도 계산
top_10_relative = relative_counts.head(10)
print(top_10)
print('\n')
print(top_10_relative)

직업
직장인          29161
대학생          22963
취업준비(휴식)      6179
군인            3802
자영업/프리랜서      3632
학생(초/중/고)     1839
학생            1751
주부            1681
회사원            874
대학원생           368
Name: count, dtype: int64


직업
직장인          0.376028
대학생          0.296106
취업준비(휴식)     0.079678
군인           0.049026
자영업/프리랜서     0.046834
학생(초/중/고)    0.023714
학생           0.022579
주부           0.021676
회사원          0.011270
대학원생         0.004745
Name: proportion, dtype: float64


In [123]:
value_counts2 = df['내원동기'].value_counts()
relative_counts2 = df['내원동기'].value_counts(normalize=True)

top_10_motive = value_counts2.head(10)
top_10_relative = relative_counts2.head(10)
print(top_10_motive)
print('\n')
print(top_10_relative)

내원동기
소개고객        30827
소개미확인       10562
광고          10524
홈페이지         7291
소개직원         6116
B2B(기업)      5282
B2B(군인)      3088
B2B(비앤빛)     1330
바이럴          1134
VIP고객관리팀      979
Name: count, dtype: int64


내원동기
소개고객        0.397511
소개미확인       0.136196
광고          0.135706
홈페이지        0.094017
소개직원        0.078865
B2B(기업)     0.068111
B2B(군인)     0.039819
B2B(비앤빛)    0.017150
바이럴         0.014623
VIP고객관리팀    0.012624
Name: proportion, dtype: float64
